
# 使用完全随机树的哈希特征变换

RandomTreesEmbedding 提供了一种将数据映射到非常高维稀疏表示的方法，这可能对分类有利。
这种映射是完全无监督且非常高效的。

此示例可视化了几棵树给出的分区，并展示了如何将这种变换用于非线性降维或非线性分类。

相邻的点通常共享同一棵树的叶子，因此共享其哈希表示的大部分。这使得仅基于截断 SVD 的变换数据的主成分就可以简单地分离两个同心圆。

在高维空间中，线性分类器通常能达到极高的准确性。对于稀疏二元数据，BernoulliNB 特别适合。底部一行比较了在变换空间中由 BernoulliNB 获得的决策边界与在原始数据上学习的 ExtraTreesClassifier 森林。


In [ ]:
import matplotlib.pyplot as plt
import numpy as np

from sklearn.datasets import make_circles
from sklearn.decomposition import TruncatedSVD
from sklearn.ensemble import ExtraTreesClassifier, RandomTreesEmbedding
from sklearn.naive_bayes import BernoulliNB

# 制作一个合成数据集
X, y = make_circles(factor=0.5, random_state=0, noise=0.05)

# 使用RandomTreesEmbedding来转换数据
hasher = RandomTreesEmbedding(n_estimators=10, random_state=0, max_depth=3)
X_transformed = hasher.fit_transform(X)

# 使用截断SVD进行降维后可视化结果
svd = TruncatedSVD(n_components=2)
X_reduced = svd.fit_transform(X_transformed)

# 在转换后的数据上学习一个朴素贝叶斯分类器
nb = BernoulliNB()
nb.fit(X_transformed, y)


# 学习一个ExtraTreesClassifier以进行比较
trees = ExtraTreesClassifier(max_depth=3, n_estimators=10, random_state=0)
trees.fit(X, y)


# 原始数据和降维数据的散点图
fig = plt.figure(figsize=(9, 8))

ax = plt.subplot(221)
ax.scatter(X[:, 0], X[:, 1], c=y, s=50, edgecolor="k")
ax.set_title("Original Data (2d)")
ax.set_xticks(())
ax.set_yticks(())

ax = plt.subplot(222)
ax.scatter(X_reduced[:, 0], X_reduced[:, 1], c=y, s=50, edgecolor="k")
ax.set_title(
    "Truncated SVD reduction (2d) of transformed data (%dd)" % X_transformed.shape[1]
)
ax.set_xticks(())
ax.set_yticks(())

# 在原始空间中绘制决策。为此，我们将为网格 [x_min, x_max]x[y_min, y_max] 中的每个点分配一个颜色。
h = 0.01
x_min, x_max = X[:, 0].min() - 0.5, X[:, 0].max() + 0.5
y_min, y_max = X[:, 1].min() - 0.5, X[:, 1].max() + 0.5
xx, yy = np.meshgrid(np.arange(x_min, x_max, h), np.arange(y_min, y_max, h))

# 使用随机树嵌入变换网格
transformed_grid = hasher.transform(np.c_[xx.ravel(), yy.ravel()])
y_grid_pred = nb.predict_proba(transformed_grid)[:, 1]

ax = plt.subplot(223)
ax.set_title("Naive Bayes on Transformed data")
ax.pcolormesh(xx, yy, y_grid_pred.reshape(xx.shape))
ax.scatter(X[:, 0], X[:, 1], c=y, s=50, edgecolor="k")
ax.set_ylim(-1.4, 1.4)
ax.set_xlim(-1.4, 1.4)
ax.set_xticks(())
ax.set_yticks(())

# 使用ExtraTreesClassifier转换网格
y_grid_pred = trees.predict_proba(np.c_[xx.ravel(), yy.ravel()])[:, 1]

ax = plt.subplot(224)
ax.set_title("ExtraTrees predictions")
ax.pcolormesh(xx, yy, y_grid_pred.reshape(xx.shape))
ax.scatter(X[:, 0], X[:, 1], c=y, s=50, edgecolor="k")
ax.set_ylim(-1.4, 1.4)
ax.set_xlim(-1.4, 1.4)
ax.set_xticks(())
ax.set_yticks(())

plt.tight_layout()
plt.show()